In [1]:
latest_gameweek = 5

In [2]:
import pandas as pd
import numpy as np
from pathlib import Path
from pulp import LpMaximize, LpProblem, LpStatus, lpSum, LpVariable

# Solver

In [3]:
def optimize(df, max_price, expected_column, captain_double_points=True):
    '''Function for solving the optimization problem.'''    
    # PRELIMINARIES

    # Create the model
    model = LpProblem(name="FPL", sense=LpMaximize)    
    variables = [LpVariable(name=f'{ix}', cat='Binary') for ix in df.index]
    captaincy_variables = [LpVariable(name=f'cap_{ix}', cat='Binary') for ix in df.index]
    prices = [df.loc[ix,'price'] for ix in df.index]
    # measure of player quality
    expected_points = [df.loc[ix,expected_column] for ix in df.index]
    goalkeepers = [1.0 if df.loc[ix,'position']=='GK' else 0.0 for ix in df.index]
    defenders = [1.0 if df.loc[ix,'position']=='DEF' else 0.0 for ix in df.index]
    midfielders = [1.0 if df.loc[ix,'position']=='MID' else 0.0 for ix in df.index]
    forwards = [1.0 if df.loc[ix,'position']=='FWD' else 0.0 for ix in df.index]
    teams = []
    for team in df['team'].unique():
        teams.append( [1.0 if df.loc[ix,'team']==team else 0.0 for ix in df.index] )

    # CONSTRAINTS

    # select 11 players
    model += lpSum(variables) == 11
    # select 1 captain
    model += lpSum(captaincy_variables) == 1
    # captain must be one of the 11 players in the team
    for i in range(0,len(variables)):
        model += captaincy_variables[i] <= variables[i]
    # set maximum price for starting 11
    model += np.dot(prices,variables) <= max_price
    # only 1 goalkeeper
    model += np.dot(goalkeepers,variables) == 1
    # at least 3 defenders
    model += np.dot(defenders,variables) >= 3
    # at most 5 defenders
    model += np.dot(defenders,variables) <= 5
    # at most 5 midfielders
    model += np.dot(midfielders,variables) <= 5
    # at least 1 forward
    model += np.dot(forwards,variables) >= 1
    # at most 3 forwards
    model += np.dot(forwards,variables) <= 3
    # max 3 players from any given team
    for team in teams:
        model += np.dot(team,variables) <= 3

    # OBJECTIVE
    if captain_double_points:
        # the second part doubles the captain's points
        model += np.dot(expected_points,variables) + np.dot(expected_points,captaincy_variables)
    else:
        model += np.dot(expected_points,variables)

    # SOLVE OPTIMIZATION

    status = model.solve()
    print(f'Status: {LpStatus[model.status]}')
    #print(f'Mean total points per gameweek: {model.objective.value()}')

    players = [str(var) for var in model.variables() if var.value()==1]
    captain = [player for player in players if 'cap' in player]
    captain = int(captain[0].replace('cap_', ''))
    players = [int(player) for player in players if 'cap' not in player]
    dream_team = df.loc[players]
    cost = (dream_team['price']).sum()
    exp_points = dream_team[expected_column].sum() + df.loc[captain, expected_column]
    print(f'Cost: {cost}')
    print(f'Expected points per week: {exp_points}')
    
    display(dream_team[['position','name', 'team', 'price', expected_column]].sort_values('position'))
    
    return players

# Data

In [4]:
path = Path(f'../data/predictions/gameweek{latest_gameweek}.csv')
projections = pd.read_csv(path, index_col=0)
projections.head(5)

name  element_type  home  corners_and_indirect_freekicks_order  \
0  Aaron Hickey             2     1                                   NaN   
1  Aaron Hickey             2     0                                   NaN   
2  Aaron Hickey             2     0                                   NaN   
3  Aaron Hickey             2     1                                   NaN   
4  Aaron Hickey             2     0                                   NaN   

   creativity_rank  direct_freekicks_order  ict_index_rank  influence_rank  \
0              222                     NaN             217             199   
1              222                     NaN             217             199   
2              222                     NaN             217             199   
3              222                     NaN             217             199   
4              222                     NaN             217             199   

   minutes  now_cost  ...  gameweek_xG_expanding_per90  \
0      400        45  ...                     0.029032   
1      400        45  ...                     0.029032   
2      400        45  ...                     0.029032   
3      400        45  ...                     0.029032   
4      400        45  ...                     0.029032   

   gameweek_xA_expanding_per90  gameweek_xGA_expanding_per90  \
0                     0.025894                      1.206016   
1                     0.025894                      1.206016   
2                     0.025894                      1.206016   
3                     0.025894                      1.206016   
4                     0.025894                      1.206016   

   gameweek_xPoints_expanding_per90  xG_overperformance  team_name  \
0                          3.377218                 0.0  Brentford   
1                          3.377218                 0.0  Brentford   
2                          3.377218                 0.0  Brentford   
3                          3.377218                 0.0  Brentford   
4                          3.377218                 0.0  Brentford   

       opponent_team                  date  gameweek  expected_points  
0            Everton  2023-09-23T16:30:00Z         6         2.748429  
1  Nottingham Forest  2023-10-01T13:00:00Z         7         2.800439  
2     Manchester Utd  2023-10-07T14:00:00Z         8         2.012874  
3            Burnley  2023-10-21T14:00:00Z         9         2.806271  
4            Chelsea  2023-10-28T11:30:00Z        10         2.178333  

[5 rows x 113 columns]

In [5]:
# decay for future projected points to model uncertainty increasing over time
decay_coeff = 0.875
projections['expected_points_with_decay'] = ( projections['expected_points']*decay_coeff
                                              **(projections['gameweek']-1) )
projections.head(5)

name  element_type  home  corners_and_indirect_freekicks_order  \
0  Aaron Hickey             2     1                                   NaN   
1  Aaron Hickey             2     0                                   NaN   
2  Aaron Hickey             2     0                                   NaN   
3  Aaron Hickey             2     1                                   NaN   
4  Aaron Hickey             2     0                                   NaN   

   creativity_rank  direct_freekicks_order  ict_index_rank  influence_rank  \
0              222                     NaN             217             199   
1              222                     NaN             217             199   
2              222                     NaN             217             199   
3              222                     NaN             217             199   
4              222                     NaN             217             199   

   minutes  now_cost  ...  gameweek_xA_expanding_per90  \
0      400        45  ...                     0.025894   
1      400        45  ...                     0.025894   
2      400        45  ...                     0.025894   
3      400        45  ...                     0.025894   
4      400        45  ...                     0.025894   

   gameweek_xGA_expanding_per90  gameweek_xPoints_expanding_per90  \
0                      1.206016                          3.377218   
1                      1.206016                          3.377218   
2                      1.206016                          3.377218   
3                      1.206016                          3.377218   
4                      1.206016                          3.377218   

   xG_overperformance  team_name      opponent_team                  date  \
0                 0.0  Brentford            Everton  2023-09-23T16:30:00Z   
1                 0.0  Brentford  Nottingham Forest  2023-10-01T13:00:00Z   
2                 0.0  Brentford     Manchester Utd  2023-10-07T14:00:00Z   
3                 0.0  Brentford            Burnley  2023-10-21T14:00:00Z   
4                 0.0  Brentford            Chelsea  2023-10-28T11:30:00Z   

   gameweek  expected_points  expected_points_with_decay  
0         6         2.748429                    1.409694  
1         7         2.800439                    1.256824  
2         8         2.012874                    0.790448  
3         9         2.806271                    0.964260  
4        10         2.178333                    0.654933  

[5 rows x 114 columns]

In [6]:
#my_gameweeks = np.arange(latest_gameweek+1, latest_gameweek+11, 1)
#my_gameweeks = np.arange(latest_gameweek+1, latest_gameweek+4, 1)
my_gameweeks = np.arange(latest_gameweek+2, latest_gameweek+12, 1)
df = projections[projections['gameweek'].isin(my_gameweeks)].groupby(by=['name', 'team_name']).sum()\
                                                        [['expected_points','expected_points_with_decay']]
df['number_of_games'] = (
    projections[projections['gameweek']
    .isin(my_gameweeks)]
    .groupby(['name', 'team_name'])
    .count()['element_type']
)

df = df.reset_index()

df['position'] = [projections.loc[projections['name']==name, 'element_type'].values[0] for name in df['name']]
position_dict={1:'GK', 2:'DEF', 3:'MID', 4:'FWD'}
df['position'] = df['position'].map(position_dict)
df['position'] = pd.Categorical(df['position'], ['GK','DEF','MID','FWD'])

df['price'] = [projections.loc[projections['name']==name, 'now_cost'].values[0] for name in df['name']]
df['price'] = df['price'] / 10.0

df['team'] = [projections.loc[projections['name']==name, 'team_name'].values[0] for name in df['name']]

df

name       team_name  expected_points  \
0                Aaron Hickey       Brentford        21.562483   
1              Aaron Ramsdale         Arsenal        33.134055   
2                Aaron Ramsey         Burnley        18.049722   
3           Aaron Wan-Bissaka  Manchester Utd        27.349504   
4          Abdoulaye Doucouré         Everton        33.033878   
..                        ...             ...              ...   
410               Yoane Wissa       Brentford        33.764197   
411           Youri Tielemans     Aston Villa        23.094264   
412  Youssef Ramalho Chermiti         Everton         8.747494   
413             Yves Bissouma       Tottenham        24.584921   
414              Zeki Amdouni         Burnley        25.753308   

     expected_points_with_decay  number_of_games position  price  \
0                      6.076444                9      DEF    4.5   
1                      9.058414                9       GK    5.0   
2                      5.369611               10      MID    5.0   
3                      7.706707                9      DEF    4.6   
4                      9.319349                9      MID    5.5   
..                          ...              ...      ...    ...   
410                    9.499260                9      FWD    6.1   
411                    6.479949                9      MID    5.8   
412                    2.495855                9      FWD    4.9   
413                    6.947812                9      MID    5.0   
414                    7.636840               10      FWD    5.4   

               team  
0         Brentford  
1           Arsenal  
2           Burnley  
3    Manchester Utd  
4           Everton  
..              ...  
410       Brentford  
411     Aston Villa  
412         Everton  
413       Tottenham  
414         Burnley  

[415 rows x 8 columns]

# Optimization

In [7]:
team_value = 100.2
money_in_the_bank = 0.3
allowed_bench_value = 17.5
max_price = team_value + money_in_the_bank - allowed_bench_value

In [8]:
ban = []

# ban some cheap keepers in good teams who don't actually play
cheap_keepers = []
cheap_keepers_ix = df[df['name'].isin(cheap_keepers)].index
ban = ban + list(cheap_keepers_ix)

# ban given outfield players
ban_field = ['Kevin De Bruyne']
ban_field_ix = df[df['name'].isin(ban_field)].index
ban = ban + list(ban_field_ix)

my_df = df.drop(ban).copy()

In [9]:
players = optimize(my_df, max_price, 'expected_points_with_decay')

Welcome to the CBC MILP Solver 
Version: 2.10.3 
Build Date: Dec 15 2019 

command line - /Users/jaakkotoivonen/Documents/my_stuff/Fantasy-Premier-League/venv23-24/lib/python3.10/site-packages/pulp/solverdir/cbc/osx/64/cbc /var/folders/ml/jr8p__z97xx1jjb90rwg7hfm0000gn/T/b6e5f3b9394047d5929c670ac874e1ef-pulp.mps max timeMode elapsed branch printingOptions all solution /var/folders/ml/jr8p__z97xx1jjb90rwg7hfm0000gn/T/b6e5f3b9394047d5929c670ac874e1ef-pulp.sol (default strategy 1)
At line 2 NAME          MODEL
At line 3 ROWS
At line 448 COLUMNS
At line 6030 RHS
At line 6474 BOUNDS
At line 7303 ENDATA
Problem MODEL has 443 rows, 828 columns and 3097 elements
Coin0008I MODEL read with 0 errors
Option for timeMode changed from cpu to elapsed
Continuous objective value is 150.654 - 0.00 seconds
Cgl0004I processed model has 441 rows, 828 columns (828 integer (828 of which binary)) and 2898 elements
Cbc0038I Initial state - 2 integers unsatisfied sum - 0.666667
Cbc0038I Solution found of -150.0

position                    name             team  price  \
16        GK         Alphonse Areola         West Ham    4.1   
226      DEF         Kieran Trippier    Newcastle Utd    6.5   
23       DEF        Andrew Robertson        Liverpool    6.5   
391      DEF  Trent Alexander-Arnold        Liverpool    7.9   
169      MID          James Maddison        Tottenham    7.9   
179      MID            Jarrod Bowen         West Ham    7.1   
290      MID           Mohamed Salah        Liverpool   12.5   
59       MID            Bryan Mbeumo        Brentford    6.9   
60       MID             Bukayo Saka          Arsenal    8.7   
213      FWD          Julián Álvarez  Manchester City    6.8   
318      FWD           Ollie Watkins      Aston Villa    7.9   

     expected_points_with_decay  
16                     9.368143  
226                   10.814779  
23                    11.659587  
391                   12.223591  
169                   13.091785  
179                   13.224134  
290                   15.348881  
59                    11.875325  
60                    13.756382  
213                   11.738416  
318                   11.997017

In [10]:
sigma=0.5
simulation_rounds = 500
next_gameweek=latest_gameweek+1

ban = []

# ban some cheap keepers in good teams who don't actually play
cheap_keepers = []
cheap_keepers_ix = df[df['name'].isin(cheap_keepers)].index
ban = ban + list(cheap_keepers_ix)

# ban given outfield players
ban_field = ['Kevin De Bruyne']
ban_field_ix = df[df['name'].isin(ban_field)].index
ban = ban + list(ban_field_ix)

results = []
for i in range(simulation_rounds):
 
    # add random noise to expected points (a fixed offset for every projection of any given player)
    projections['expected_points_with_noise'] = (projections
    .groupby('name')
    .apply(lambda x: x['expected_points']+np.random.normal(0,sigma))
    .reset_index()
    .sort_values('level_1')
    ['expected_points']
    .values
    )

    # decay
    projections['expected_points_with_noise_with_decay'] = ( projections['expected_points_with_noise']*decay_coeff
                                              **(projections['gameweek']-next_gameweek) )

    df['expected_points_with_noise_with_decay'] = projections[projections['gameweek'].isin(my_gameweeks)].groupby(by=['name', 'team_name']).sum()\
                                                            ['expected_points_with_noise_with_decay'].values

    my_df = df.drop(ban).copy()
    
    players = optimize(my_df, max_price, 'expected_points_with_noise_with_decay')

    results.append(players)
    

Welcome to the CBC MILP Solver 
Version: 2.10.3 
Build Date: Dec 15 2019 

command line - /Users/jaakkotoivonen/Documents/my_stuff/Fantasy-Premier-League/venv23-24/lib/python3.10/site-packages/pulp/solverdir/cbc/osx/64/cbc /var/folders/ml/jr8p__z97xx1jjb90rwg7hfm0000gn/T/25203a8fcc38422e9fa7aef03e1ee5d7-pulp.mps max timeMode elapsed branch printingOptions all solution /var/folders/ml/jr8p__z97xx1jjb90rwg7hfm0000gn/T/25203a8fcc38422e9fa7aef03e1ee5d7-pulp.sol (default strategy 1)
At line 2 NAME          MODEL
At line 3 ROWS
At line 448 COLUMNS
At line 6030 RHS
At line 6474 BOUNDS
At line 7303 ENDATA
Problem MODEL has 443 rows, 828 columns and 3097 elements
Coin0008I MODEL read with 0 errors
Option for timeMode changed from cpu to elapsed
Continuous objective value is 315.735 - 0.00 seconds
Cgl0004I processed model has 441 rows, 828 columns (828 integer (828 of which binary)) and 2898 elements
Cbc0038I Initial state - 2 integers unsatisfied sum - 0.876712
Cbc0038I Solution found of -313.9

position                    name             team  price  \
135       GK       Guglielmo Vicario        Tottenham    5.1   
226      DEF         Kieran Trippier    Newcastle Utd    6.5   
23       DEF        Andrew Robertson        Liverpool    6.5   
48       DEF          Benjamin White          Arsenal    5.5   
220      MID            Kaoru Mitoma         Brighton    6.5   
290      MID           Mohamed Salah        Liverpool   12.5   
57       MID  Bruno Borges Fernandes   Manchester Utd    8.4   
59       MID            Bryan Mbeumo        Brentford    6.9   
60       MID             Bukayo Saka          Arsenal    8.7   
213      FWD          Julián Álvarez  Manchester City    6.8   
318      FWD           Ollie Watkins      Aston Villa    7.9   

     expected_points_with_noise_with_decay  
135                              22.164189  
226                              24.072590  
23                               24.001850  
48                               21.811690  
220                              26.154430  
290                              31.509622  
57                               27.317025  
59                               25.802541  
60                               27.385087  
213                              24.743238  
318                              27.805075

Welcome to the CBC MILP Solver 
Version: 2.10.3 
Build Date: Dec 15 2019 

command line - /Users/jaakkotoivonen/Documents/my_stuff/Fantasy-Premier-League/venv23-24/lib/python3.10/site-packages/pulp/solverdir/cbc/osx/64/cbc /var/folders/ml/jr8p__z97xx1jjb90rwg7hfm0000gn/T/711047f6f33e47c59de0e2ea69ecbd68-pulp.mps max timeMode elapsed branch printingOptions all solution /var/folders/ml/jr8p__z97xx1jjb90rwg7hfm0000gn/T/711047f6f33e47c59de0e2ea69ecbd68-pulp.sol (default strategy 1)
At line 2 NAME          MODEL
At line 3 ROWS
At line 448 COLUMNS
At line 6030 RHS
At line 6474 BOUNDS
At line 7303 ENDATA
Problem MODEL has 443 rows, 828 columns and 3097 elements
Coin0008I MODEL read with 0 errors
Option for timeMode changed from cpu to elapsed
Continuous objective value is 307.695 - 0.00 seconds
Cgl0004I processed model has 441 rows, 828 columns (828 integer (828 of which binary)) and 2898 elements
Cbc0038I Initial state - 2 integers unsatisfied sum - 0.705882
Cbc0038I Solution found of -307.0

position                    name             team  price  \
135       GK       Guglielmo Vicario        Tottenham    5.1   
23       DEF        Andrew Robertson        Liverpool    6.5   
242      DEF             Lucas Digne      Aston Villa    4.6   
276      DEF              Matty Cash      Aston Villa    4.7   
391      DEF  Trent Alexander-Arnold        Liverpool    7.9   
145      MID           Heung-Min Son        Tottenham    9.1   
157      MID           Jack Grealish  Manchester City    7.4   
290      MID           Mohamed Salah        Liverpool   12.5   
57       MID  Bruno Borges Fernandes   Manchester Utd    8.4   
60       MID             Bukayo Saka          Arsenal    8.7   
12       FWD          Alexander Isak    Newcastle Utd    7.7   

     expected_points_with_noise_with_decay  
135                              20.419316  
23                               27.395905  
242                              20.622956  
276                              21.821472  
391                              25.414885  
145                              27.014502  
157                              26.244175  
290                              30.332056  
57                               26.168347  
60                               27.521913  
12                               23.999854

Welcome to the CBC MILP Solver 
Version: 2.10.3 
Build Date: Dec 15 2019 

command line - /Users/jaakkotoivonen/Documents/my_stuff/Fantasy-Premier-League/venv23-24/lib/python3.10/site-packages/pulp/solverdir/cbc/osx/64/cbc /var/folders/ml/jr8p__z97xx1jjb90rwg7hfm0000gn/T/4348df79dc044d878237dbf296001f19-pulp.mps max timeMode elapsed branch printingOptions all solution /var/folders/ml/jr8p__z97xx1jjb90rwg7hfm0000gn/T/4348df79dc044d878237dbf296001f19-pulp.sol (default strategy 1)
At line 2 NAME          MODEL
At line 3 ROWS
At line 448 COLUMNS
At line 6030 RHS
At line 6474 BOUNDS
At line 7303 ENDATA
Problem MODEL has 443 rows, 828 columns and 3097 elements
Coin0008I MODEL read with 0 errors
Option for timeMode changed from cpu to elapsed
Continuous objective value is 315.14 - 0.00 seconds
Cgl0004I processed model has 441 rows, 828 columns (828 integer (828 of which binary)) and 2898 elements
Cbc0038I Initial state - 2 integers unsatisfied sum - 0.553191
Cbc0038I Pass   1: suminf.    0.51

...

position              name               team  price  \
275       GK       Matt Turner  Nottingham Forest    4.0   
23       DEF  Andrew Robertson          Liverpool    6.5   
330      DEF  Pervis Estupiñán           Brighton    5.3   
71       DEF    Charlie Taylor            Burnley    4.0   
145      MID     Heung-Min Son          Tottenham    9.1   
169      MID    James Maddison          Tottenham    7.9   
179      MID      Jarrod Bowen           West Ham    7.1   
60       MID       Bukayo Saka            Arsenal    8.7   
120      FWD    Erling Haaland    Manchester City   14.1   
306      FWD   Nicolas Jackson            Chelsea    7.0   
318      FWD     Ollie Watkins        Aston Villa    7.9   

     expected_points_with_noise_with_decay  
275                              20.560745  
23                               25.760777  
330                              22.370947  
71                               21.596156  
145                              26.091785  
169                              25.594530  
179                              27.918165  
60                               27.601441  
120                              31.128882  
306                              26.036499  
318                              24.521138

Welcome to the CBC MILP Solver 
Version: 2.10.3 
Build Date: Dec 15 2019 

command line - /Users/jaakkotoivonen/Documents/my_stuff/Fantasy-Premier-League/venv23-24/lib/python3.10/site-packages/pulp/solverdir/cbc/osx/64/cbc /var/folders/ml/jr8p__z97xx1jjb90rwg7hfm0000gn/T/4ceae5108ae04025a666cd424a233d9b-pulp.mps max timeMode elapsed branch printingOptions all solution /var/folders/ml/jr8p__z97xx1jjb90rwg7hfm0000gn/T/4ceae5108ae04025a666cd424a233d9b-pulp.sol (default strategy 1)
At line 2 NAME          MODEL
At line 3 ROWS
At line 448 COLUMNS
At line 6030 RHS
At line 6474 BOUNDS
At line 7303 ENDATA
Problem MODEL has 443 rows, 828 columns and 3097 elements
Coin0008I MODEL read with 0 errors
Option for timeMode changed from cpu to elapsed
Continuous objective value is 315.796 - 0.00 seconds
Cgl0004I processed model has 441 rows, 828 columns (828 integer (828 of which binary)) and 2898 elements
Cbc0038I Initial state - 2 integers unsatisfied sum - 0.319149
Cbc0038I Pass   1: suminf.    0.2

position               name             team  price  \
16        GK    Alphonse Areola         West Ham    4.1   
23       DEF   Andrew Robertson        Liverpool    6.5   
276      DEF         Matty Cash      Aston Villa    4.7   
371      DEF        Sven Botman    Newcastle Utd    4.5   
175      MID  James Ward-Prowse         West Ham    6.1   
244      MID          Luis Díaz        Liverpool    7.7   
290      MID      Mohamed Salah        Liverpool   12.5   
325      MID        Pascal Groß         Brighton    6.3   
60       MID        Bukayo Saka          Arsenal    8.7   
120      FWD     Erling Haaland  Manchester City   14.1   
213      FWD     Julián Álvarez  Manchester City    6.8   

     expected_points_with_noise_with_decay  
16                               20.908732  
23                               25.321460  
276                              22.499204  
371                              22.643995  
175                              26.014182  
244                              25.412454  
290                              31.185300  
325                              26.080994  
60                               29.782711  
120                              26.412848  
213                              26.681279

Welcome to the CBC MILP Solver 
Version: 2.10.3 
Build Date: Dec 15 2019 

command line - /Users/jaakkotoivonen/Documents/my_stuff/Fantasy-Premier-League/venv23-24/lib/python3.10/site-packages/pulp/solverdir/cbc/osx/64/cbc /var/folders/ml/jr8p__z97xx1jjb90rwg7hfm0000gn/T/78bd8e6e42c94604b378ef97d41b2759-pulp.mps max timeMode elapsed branch printingOptions all solution /var/folders/ml/jr8p__z97xx1jjb90rwg7hfm0000gn/T/78bd8e6e42c94604b378ef97d41b2759-pulp.sol (default strategy 1)
At line 2 NAME          MODEL
At line 3 ROWS
At line 448 COLUMNS
At line 6030 RHS
At line 6474 BOUNDS
At line 7303 ENDATA
Problem MODEL has 443 rows, 828 columns and 3097 elements
Coin0008I MODEL read with 0 errors
Option for timeMode changed from cpu to elapsed
Continuous objective value is 314.277 - 0.00 seconds
Cgl0004I processed model has 441 rows, 828 columns (828 integer (828 of which binary)) and 2898 elements
Cbc0038I Initial state - 2 integers unsatisfied sum - 0.8
Cbc0038I Solution found of -311.802
Cb

position                       name             team  price  \
1         GK             Aaron Ramsdale          Arsenal    5.0   
226      DEF            Kieran Trippier    Newcastle Utd    6.5   
23       DEF           Andrew Robertson        Liverpool    6.5   
39       DEF                Axel Disasi          Chelsea    5.1   
391      DEF     Trent Alexander-Arnold        Liverpool    7.9   
145      MID              Heung-Min Son        Tottenham    9.1   
169      MID             James Maddison        Tottenham    7.9   
290      MID              Mohamed Salah        Liverpool   12.5   
34       MID  Antony Matheus dos Santos   Manchester Utd    6.8   
60       MID                Bukayo Saka          Arsenal    8.7   
213      FWD             Julián Álvarez  Manchester City    6.8   

     expected_points_with_noise_with_decay  
1                                22.511939  
226                              22.822947  
23                               24.572225  
39                               22.930397  
391                              25.262159  
145                              28.906818  
169                              26.871977  
290                              30.142642  
34                               27.793394  
60                               29.648036  
213                              21.604741

In [11]:
my_df['dream_team_appearances'] = [sum(team.count(player_id) / simulation_rounds for team in results) for player_id in my_df.index]

In [12]:
print('Most appearances, all players:')
display(my_df
        .drop(['team', 'expected_points_with_noise_with_decay'], axis=1)
        .sort_values(by='dream_team_appearances', ascending=False)
        .head(20))

Most appearances, all players:


name        team_name  expected_points  \
290           Mohamed Salah        Liverpool        55.911165   
60              Bukayo Saka          Arsenal        50.030835   
391  Trent Alexander-Arnold        Liverpool        44.574034   
179            Jarrod Bowen         West Ham        46.883264   
23         Andrew Robertson        Liverpool        42.571137   
169          James Maddison        Tottenham        46.255695   
120          Erling Haaland  Manchester City        50.548490   
145           Heung-Min Son        Tottenham        46.955373   
213          Julián Álvarez  Manchester City        41.853937   
318           Ollie Watkins      Aston Villa        42.765664   
57   Bruno Borges Fernandes   Manchester Utd        45.093525   
226         Kieran Trippier    Newcastle Utd        38.315570   
59             Bryan Mbeumo        Brentford        42.304702   
335         Raheem Sterling          Chelsea        40.834489   
306         Nicolas Jackson          Chelsea        38.317698   
175       James Ward-Prowse         West Ham        41.043925   
325             Pascal Groß         Brighton        41.417286   
276              Matty Cash      Aston Villa        33.938578   
16          Alphonse Areola         West Ham        33.438992   
330        Pervis Estupiñán         Brighton        34.827417   

     expected_points_with_decay  number_of_games position  price  \
290                   15.348881                9      MID   12.5   
60                    13.756382                9      MID    8.7   
391                   12.223591                9      DEF    7.9   
179                   13.224134                9      MID    7.1   
23                    11.659587                9      DEF    6.5   
169                   13.091785                9      MID    7.9   
120                   14.067838                9      FWD   14.1   
145                   13.266446                9      MID    9.1   
213                   11.738416                9      FWD    6.8   
318                   11.997017                9      FWD    7.9   
57                    12.675156                9      MID    8.4   
226                   10.814779                9      DEF    6.5   
59                    11.875325                9      MID    6.9   
335                   11.800393                9      MID    7.2   
306                   11.018696                9      FWD    7.0   
175                   11.489890                9      MID    6.1   
325                   11.358687                9      MID    6.3   
276                    9.522172                9      DEF    4.7   
16                     9.368143                9       GK    4.1   
330                    9.526580                9      DEF    5.3   

     dream_team_appearances  
290                   0.770  
60                    0.684  
391                   0.630  
179                   0.608  
23                    0.560  
169                   0.536  
120                   0.492  
145                   0.454  
213                   0.414  
318                   0.410  
57                    0.344  
226                   0.312  
59                    0.264  
335                   0.214  
306                   0.202  
175                   0.200  
325                   0.168  
276                   0.160  
16                    0.138  
330                   0.118

In [13]:
print('GOALKEEPERS')
display(my_df
        .drop(['team', 'expected_points_with_noise_with_decay'], axis=1)
        [my_df['position']=='GK']
        .sort_values(by='dream_team_appearances', ascending=False)
        .head(20))

GOALKEEPERS


name          team_name  expected_points  \
16             Alphonse Areola           West Ham        33.438992   
96           David Raya Martin            Arsenal        34.413470   
305                  Nick Pope      Newcastle Utd        33.784272   
135          Guglielmo Vicario          Tottenham        32.889216   
112  Ederson Santana de Moraes    Manchester City        33.313445   
15       Alisson Ramses Becker          Liverpool        34.651610   
174             James Trafford            Burnley        29.409666   
1               Aaron Ramsdale            Arsenal        33.134055   
347                Robin Olsen        Aston Villa        30.182009   
50                  Bernd Leno             Fulham        30.317652   
346             Robert Sánchez            Chelsea        29.009932   
310       Norberto Murara Neto        Bournemouth        30.370112   
180               Jason Steele           Brighton        30.833447   
275                Matt Turner  Nottingham Forest        28.583178   
206        José Malheiro de Sá             Wolves        30.319975   
201            Jordan Pickford            Everton        27.593229   
118   Emiliano Martínez Romero        Aston Villa        28.113638   
263               Mark Flekken          Brentford        28.361912   
24                 André Onana     Manchester Utd        27.064476   
379            Thomas Kaminski              Luton        24.845448   

     expected_points_with_decay  number_of_games position  price  \
16                     9.368143                9       GK    4.1   
96                     9.414124                9       GK    4.8   
305                    9.562497                9       GK    5.5   
135                    9.298476                9       GK    5.1   
112                    9.406310                9       GK    5.6   
15                     9.477407                9       GK    5.5   
174                    8.707487               10       GK    4.5   
1                      9.058414                9       GK    5.0   
347                    8.479235                9       GK    4.0   
50                     8.455450                9       GK    4.6   
346                    8.463434                9       GK    4.5   
310                    8.471161                9       GK    4.5   
180                    8.411840                9       GK    4.4   
275                    7.914237                9       GK    4.0   
206                    8.257130                9       GK    5.0   
201                    7.849455                9       GK    4.4   
118                    7.886822                9       GK    4.9   
263                    8.013367                9       GK    4.5   
24                     7.606773                9       GK    5.0   
379                    7.441519               10       GK    4.5   

     dream_team_appearances  
16                    0.138  
96                    0.114  
305                   0.100  
135                   0.096  
112                   0.078  
15                    0.070  
174                   0.068  
1                     0.062  
347                   0.042  
50                    0.042  
346                   0.040  
310                   0.034  
180                   0.028  
275                   0.018  
206                   0.014  
201                   0.012  
118                   0.010  
263                   0.008  
24                    0.008  
379                   0.008

In [14]:
print('DEFENDERS')
display(my_df
        .drop(['team', 'expected_points_with_noise_with_decay'], axis=1)
        [my_df['position']=='DEF']
        .sort_values(by='dream_team_appearances', ascending=False)
        .head(20))

DEFENDERS


name        team_name  expected_points  \
391  Trent Alexander-Arnold        Liverpool        44.574034   
23         Andrew Robertson        Liverpool        42.571137   
226         Kieran Trippier    Newcastle Utd        38.315570   
276              Matty Cash      Aston Villa        33.938578   
248               Luke Shaw   Manchester Utd        34.430339   
330        Pervis Estupiñán         Brighton        34.827417   
71           Charlie Taylor          Burnley        29.855924   
42             Ben Chilwell          Chelsea        32.816064   
251      Mads Juel Andersen            Luton        28.633702   
371             Sven Botman    Newcastle Utd        31.772865   
355   Rúben Gato Alves Dias  Manchester City        32.244245   
48           Benjamin White          Arsenal        34.236165   
100          Destiny Udogie        Tottenham        31.742836   
39              Axel Disasi          Chelsea        29.741095   
86          Cristian Romero        Tottenham        30.788087   
328             Pedro Porro        Tottenham        32.178767   
189        Joachim Andersen   Crystal Palace        32.275888   
230             Kyle Walker  Manchester City        30.429954   
406          William Saliba          Arsenal        32.479807   
235            Levi Colwill          Chelsea        29.258418   

     expected_points_with_decay  number_of_games position  price  \
391                   12.223591                9      DEF    7.9   
23                    11.659587                9      DEF    6.5   
226                   10.814779                9      DEF    6.5   
276                    9.522172                9      DEF    4.7   
248                    9.699316                9      DEF    5.5   
330                    9.526580                9      DEF    5.3   
71                     8.825719               10      DEF    4.0   
42                     9.533047                9      DEF    5.8   
251                    8.596231               10      DEF    4.0   
371                    9.007510                9      DEF    4.5   
355                    9.109913                9      DEF    5.5   
48                     9.368813                9      DEF    5.5   
100                    8.987775                9      DEF    4.7   
39                     8.664155                9      DEF    5.1   
86                     8.714184                9      DEF    4.7   
328                    9.103507                9      DEF    5.0   
189                    8.798817                9      DEF    4.6   
230                    8.588394                9      DEF    5.2   
406                    8.869954                9      DEF    5.2   
235                    8.516137                9      DEF    4.5   

     dream_team_appearances  
391                   0.630  
23                    0.560  
226                   0.312  
276                   0.160  
248                   0.118  
330                   0.118  
71                    0.098  
42                    0.086  
251                   0.086  
371                   0.084  
355                   0.078  
48                    0.066  
100                   0.060  
39                    0.052  
86                    0.052  
328                   0.048  
189                   0.046  
230                   0.042  
406                   0.042  
235                   0.038

In [15]:
print('MIDFIELDERS')
display(my_df
        .drop(['team', 'expected_points_with_noise_with_decay'], axis=1)
        [my_df['position']=='MID']
        .sort_values(by='dream_team_appearances', ascending=False)
        .head(20))

MIDFIELDERS


name        team_name  expected_points  \
290              Mohamed Salah        Liverpool        55.911165   
60                 Bukayo Saka          Arsenal        50.030835   
179               Jarrod Bowen         West Ham        46.883264   
169             James Maddison        Tottenham        46.255695   
145              Heung-Min Son        Tottenham        46.955373   
57      Bruno Borges Fernandes   Manchester Utd        45.093525   
59                Bryan Mbeumo        Brentford        42.304702   
335            Raheem Sterling          Chelsea        40.834489   
175          James Ward-Prowse         West Ham        41.043925   
325                Pascal Groß         Brighton        41.417286   
264            Martin Ødegaard          Arsenal        42.421948   
220               Kaoru Mitoma         Brighton        39.019257   
331                 Phil Foden  Manchester City        39.677126   
157              Jack Grealish  Manchester City        39.007255   
294               Moussa Diaby      Aston Villa        37.673258   
110               Eberechi Eze   Crystal Palace        38.159537   
260            Marcus Rashford   Manchester Utd        40.745709   
370                Solly March         Brighton        37.044451   
34   Antony Matheus dos Santos   Manchester Utd        35.570269   
99            Dejan Kulusevski        Tottenham        35.881378   

     expected_points_with_decay  number_of_games position  price  \
290                   15.348881                9      MID   12.5   
60                    13.756382                9      MID    8.7   
179                   13.224134                9      MID    7.1   
169                   13.091785                9      MID    7.9   
145                   13.266446                9      MID    9.1   
57                    12.675156                9      MID    8.4   
59                    11.875325                9      MID    6.9   
335                   11.800393                9      MID    7.2   
175                   11.489890                9      MID    6.1   
325                   11.358687                9      MID    6.3   
264                   11.638243                9      MID    8.5   
220                   10.714615                9      MID    6.5   
331                   11.136300                9      MID    7.6   
157                   10.936317                9      MID    7.4   
294                   10.570264                9      MID    6.6   
110                   10.449954                9      MID    6.3   
260                   11.442970                9      MID    8.9   
370                   10.149939                9      MID    6.6   
34                    10.003810                9      MID    6.8   
99                    10.127294                9      MID    7.0   

     dream_team_appearances  
290                   0.770  
60                    0.684  
179                   0.608  
169                   0.536  
145                   0.454  
57                    0.344  
59                    0.264  
335                   0.214  
175                   0.200  
325                   0.168  
264                   0.094  
220                   0.084  
331                   0.076  
157                   0.068  
294                   0.058  
110                   0.056  
260                   0.046  
370                   0.026  
34                    0.022  
99                    0.018

In [16]:
print('FORWARDS')
display(my_df
        .drop(['team', 'expected_points_with_noise_with_decay'], axis=1)
        [my_df['position']=='FWD']
        .sort_values(by='dream_team_appearances', ascending=False)
        .head(20))

FORWARDS


name          team_name  expected_points  \
120        Erling Haaland    Manchester City        50.548490   
213        Julián Álvarez    Manchester City        41.853937   
318         Ollie Watkins        Aston Villa        42.765664   
306       Nicolas Jackson            Chelsea        38.317698   
63          Callum Wilson      Newcastle Utd        37.331150   
12         Alexander Isak      Newcastle Utd        36.125637   
68         Carlton Morris              Luton        30.462750   
313       Odsonne Edouard     Crystal Palace        34.097305   
283       Michail Antonio           West Ham        33.069100   
410           Yoane Wissa          Brentford        33.764197   
250           Lyle Foster            Burnley        29.441129   
122         Evan Ferguson           Brighton        33.585829   
373         Taiwo Awoniyi  Nottingham Forest        33.615233   
106       Dominic Solanke        Bournemouth        33.616026   
81             Cody Gakpo          Liverpool        33.723769   
94   Darwin Núñez Ribeiro          Liverpool        32.199711   
159           Jacob Brown              Luton        19.137888   
92          Danny Welbeck           Brighton        29.339388   
337        Rasmus Højlund     Manchester Utd        25.349314   
315       Oliver McBurnie      Sheffield Utd        18.746263   

     expected_points_with_decay  number_of_games position  price  \
120                   14.067838                9      FWD   14.1   
213                   11.738416                9      FWD    6.8   
318                   11.997017                9      FWD    7.9   
306                   11.018696                9      FWD    7.0   
63                    10.520008                9      FWD    7.8   
12                    10.173810                9      FWD    7.7   
68                     9.140867               10      FWD    5.5   
313                    9.331261                9      FWD    5.6   
283                    9.322258                9      FWD    6.0   
410                    9.499260                9      FWD    6.1   
250                    8.721734               10      FWD    5.0   
122                    9.184054                9      FWD    6.0   
373                    9.341463                9      FWD    6.6   
106                    9.371177                9      FWD    6.5   
81                     9.250132                9      FWD    7.3   
94                     8.823236                9      FWD    7.4   
159                    5.737698               10      FWD    4.9   
92                     8.010914                9      FWD    5.8   
337                    7.124313                9      FWD    7.0   
315                    5.263101                9      FWD    5.4   

     dream_team_appearances  
120                   0.492  
213                   0.414  
318                   0.410  
306                   0.202  
63                    0.094  
12                    0.062  
68                    0.044  
313                   0.040  
283                   0.034  
410                   0.030  
250                   0.026  
122                   0.022  
373                   0.022  
106                   0.020  
81                    0.010  
94                    0.006  
159                   0.002  
92                    0.002  
337                   0.002  
315                   0.000

In [17]:
players = optimize(my_df, max_price, 'dream_team_appearances', captain_double_points=False)

Welcome to the CBC MILP Solver 
Version: 2.10.3 
Build Date: Dec 15 2019 

command line - /Users/jaakkotoivonen/Documents/my_stuff/Fantasy-Premier-League/venv23-24/lib/python3.10/site-packages/pulp/solverdir/cbc/osx/64/cbc /var/folders/ml/jr8p__z97xx1jjb90rwg7hfm0000gn/T/d615f75410b9417189ef2848afb6c6f0-pulp.mps max timeMode elapsed branch printingOptions all solution /var/folders/ml/jr8p__z97xx1jjb90rwg7hfm0000gn/T/d615f75410b9417189ef2848afb6c6f0-pulp.sol (default strategy 1)
At line 2 NAME          MODEL
At line 3 ROWS
At line 448 COLUMNS
At line 5339 RHS
At line 5783 BOUNDS
At line 6612 ENDATA
Problem MODEL has 443 rows, 828 columns and 3097 elements
Coin0008I MODEL read with 0 errors
Option for timeMode changed from cpu to elapsed
Continuous objective value is 5.38236 - 0.00 seconds
Cgl0004I processed model has 441 rows, 828 columns (828 integer (828 of which binary)) and 2898 elements
Cutoff increment increased from 1e-05 to 0.001998
Cbc0038I Initial state - 2 integers unsatisfie

position                    name             team  price  \
16        GK         Alphonse Areola         West Ham    4.1   
226      DEF         Kieran Trippier    Newcastle Utd    6.5   
23       DEF        Andrew Robertson        Liverpool    6.5   
391      DEF  Trent Alexander-Arnold        Liverpool    7.9   
169      MID          James Maddison        Tottenham    7.9   
179      MID            Jarrod Bowen         West Ham    7.1   
290      MID           Mohamed Salah        Liverpool   12.5   
59       MID            Bryan Mbeumo        Brentford    6.9   
60       MID             Bukayo Saka          Arsenal    8.7   
213      FWD          Julián Álvarez  Manchester City    6.8   
318      FWD           Ollie Watkins      Aston Villa    7.9   

     dream_team_appearances  
16                    0.138  
226                   0.312  
23                    0.560  
391                   0.630  
169                   0.536  
179                   0.608  
290                   0.770  
59                    0.264  
60                    0.684  
213                   0.414  
318                   0.410

In [18]:
projections[(projections.gameweek==(latest_gameweek+1))].sort_values('expected_points', ascending=False)[['name', 'expected_points']].head(20)

name  expected_points
2931              Mohamed Salah         6.174186
1213             Erling Haaland         5.737630
606                 Bukayo Saka         5.579394
2254            Kevin De Bruyne         5.391571
2153             Julián Álvarez         5.214999
3282                Pascal Groß         5.183874
576      Bruno Borges Fernandes         5.159112
596                Bryan Mbeumo         5.128398
3343                 Phil Foden         5.122905
1586              Jack Grealish         5.065041
3950     Trent Alexander-Arnold         5.042111
1112               Eberechi Eze         4.943719
2224               Kaoru Mitoma         4.867701
3383            Raheem Sterling         4.825781
236            Andrew Robertson         4.816112
2284            Kieran Trippier         4.695527
3737                Solly March         4.676314
2669            Martin Ødegaard         4.590195
636               Callum Wilson         4.566433
1132  Ederson Santana de Moraes         4.545441

In [ ]:
display(projections[projections.name.str.contains('Saliba')][['name', 'expected_points']])
display(projections[projections.name.str.contains('Saliba')][['expected_points_with_decay']].sum())